In this notebook we will index the french dump version of the wikipedia dataset, and use with the retrieval for our qa/system

In [1]:
import numpy as np

In [2]:
import numpy as np
from haystack.utils import clean_wiki_text, convert_files_to_docs, fetch_archive_from_http, print_answers

In [3]:
from datasets import load_dataset

In [4]:
wiki_corpus = load_dataset("wikipedia", "20220301.fr", split="train")

WARNING - datasets.load -  Using the latest cached version of the module from /Users/es.py/.cache/huggingface/modules/datasets_modules/datasets/wikipedia/aa542ed919df55cc5d3347f42dd4521d05ca68751f50dbc32bae2a7f1e167559 (last modified on Wed Jul 13 11:01:44 2022) since it couldn't be found locally at wikipedia., or remotely on the Hugging Face Hub.
WARNING - datasets.builder -  Reusing dataset wikipedia (/Users/es.py/.cache/huggingface/datasets/wikipedia/20220301.fr/2.0.0/aa542ed919df55cc5d3347f42dd4521d05ca68751f50dbc32bae2a7f1e167559)


In [5]:
wiki_corpus = wiki_corpus.shuffle(seed=42)

WARNING - datasets.arrow_dataset -  Loading cached shuffled indices for dataset at /Users/es.py/.cache/huggingface/datasets/wikipedia/20220301.fr/2.0.0/aa542ed919df55cc5d3347f42dd4521d05ca68751f50dbc32bae2a7f1e167559/cache-a0a7d2df10490c15.arrow


In [6]:
sample_wiki = wiki_corpus.shard(100, index=0)

In [7]:
sample_doc_dict = sample_wiki[1]

In [8]:
from haystack.schema import Document

In [9]:
docs = Document.from_dict(sample_doc_dict, field_map={"text": "content"})

#### Building the Elastic Search Index

In [10]:
from haystack.utils import clean_wiki_text, convert_files_to_docs

In [11]:
from haystack.errors import HaystackError
from haystack.schema import Document
from typing import List, Optional, Generator, Set, Union, Callable, Dict
from copy import deepcopy
from haystack.nodes import PreProcessor
import re

In [12]:
from gensim.utils import deaccent

def remove_accents(document):
    input_without_accent = deaccent(document)
    return input_without_accent

In [13]:
async def convert_wiki_article_to_docs(
    item: dict,
    clean_func: Optional[Callable] = None,
    split_paragraphs: bool = False,
) -> List[Document]:
    """
    item

    :param items: dict of items
    :param clean_func: a custom cleaning function that gets applied to each doc (input: str, output:str)
    :param split_paragraphs: split text in paragraphs.
    """
    documents = []
    processed = 0
    text = item.get("text")
    text = remove_accents(text)
    if clean_func:
        text = clean_func(text)
    if split_paragraphs:
        for para in text.split("\n"):
            if 200 <= len(para.strip()) <= 2000:
                # just pick the paragraph with length between 50 and 1500
                processed += 1
                doc = Document(content=para, meta={"title": item.get("title")}, id=item.get("id"))
                documents.append(doc)
            else:
                continue
    else:
        processed += 1
        doc = Document(content=text, meta={"title": item.get("title")}, id=item.get("id"))
        documents.append(doc)
    
    return documents

In [14]:
import asyncio

#### Saving the Document in the retriever

In [15]:
from tqdm import tqdm
from tqdm.asyncio import tqdm_asyncio
from haystack.document_stores import ElasticsearchDocumentStore

In [16]:
INDEX_NAME = 'fr-wikipedia'

In [17]:

document_store = ElasticsearchDocumentStore(index=INDEX_NAME, recreate_index=False, analyzer="french")

/Users/es.py/Projects/Personal/unsupervised-open-domain-french-question-answering/.venv/lib/python3.9/site-packages/elasticsearch/connection/base.py:190: ElasticsearchDeprecationWarning: Elasticsearch built-in security features are not enabled. Without authentication, your cluster could be accessible to anyone. See https://www.elastic.co/guide/en/elasticsearch/reference/7.16/security-minimal-setup.html to enable security.
  warnings.warn(message, category=ElasticsearchDeprecationWarning)


In [18]:
def split_list_in_chunck(list_, len_):
    chunks = [list_[i:i+len_] for i in range(0, len(list_), len_)]
    return chunks

In [19]:
from elasticsearch.helpers import bulk, parallel_bulk, scan

In [20]:
from collections import deque

In [21]:

def write_documents_parallel(
        self,
        documents: Union[List[dict], List[Document]],
        index: Optional[str] = None,
        batch_size: int = 10_000,
        duplicate_documents: Optional[str] = None,
        headers: Optional[Dict[str, str]] = None,
    ):
        """
        Indexes documents for later queries in Elasticsearch./ an update for the index that use parralell bluk

        Behaviour if a document with the same ID already exists in ElasticSearch:
        a) (Default) Throw Elastic's standard error message for duplicate IDs.
        b) If `self.update_existing_documents=True` for DocumentStore: Overwrite existing documents.
        (This is only relevant if you pass your own ID when initializing a `Document`.
        If don't set custom IDs for your Documents or just pass a list of dictionaries here,
        they will automatically get UUIDs assigned. See the `Document` class for details)

        :param documents: a list of Python dictionaries or a list of Haystack Document objects.
                          For documents as dictionaries, the format is {"content": "<the-actual-text>"}.
                          Optionally: Include meta data via {"content": "<the-actual-text>",
                          "meta":{"name": "<some-document-name>, "author": "somebody", ...}}
                          It can be used for filtering and is accessible in the responses of the Finder.
                          Advanced: If you are using your own Elasticsearch mapping, the key names in the dictionary
                          should be changed to what you have set for self.content_field and self.name_field.
        :param index: Elasticsearch index where the documents should be indexed. If not supplied, self.index will be used.
        :param batch_size: Number of documents that are passed to Elasticsearch's bulk function at a time.
        :param duplicate_documents: Handle duplicates document based on parameter options.
                                    Parameter options : ( 'skip','overwrite','fail')
                                    skip: Ignore the duplicates documents
                                    overwrite: Update any existing documents with the same ID when adding documents.
                                    fail: an error is raised if the document ID of the document being added already
                                    exists.
        :param headers: Custom HTTP headers to pass to elasticsearch client (e.g. {'Authorization': 'Basic YWRtaW46cm9vdA=='})
                Check out https://www.elastic.co/guide/en/elasticsearch/reference/current/http-clients.html for more information.
        :raises DuplicateDocumentError: Exception trigger on duplicate document
        :return: None
        """
        print("I am inside the function")
        if index and not self.client.indices.exists(index=index, headers=headers):
            self._create_document_index(index, headers=headers)

        if index is None:
            index = self.index
        duplicate_documents = duplicate_documents or self.duplicate_documents
        assert (
            duplicate_documents in self.duplicate_documents_options
        ), f"duplicate_documents parameter must be {', '.join(self.duplicate_documents_options)}"

        field_map = self._create_document_field_map()
        document_objects = [Document.from_dict(d, field_map=field_map) if isinstance(d, dict) else d for d in documents]
        document_objects_chunk = split_list_in_chunck(document_objects, 9990)
        document_objects_deduplicated = []
        for doc_chunk in document_objects_chunk:           
            chunk_deduplicated = self._handle_duplicate_documents(documents=doc_chunk, 
                                                                  index=index, 
                                                                  duplicate_documents=duplicate_documents, 
                                                                  headers=headers)
            document_objects_deduplicated.extend(chunk_deduplicated)
        documents_to_index = []
        # split the document in chunk of 10000
        for doc in tqdm(document_objects_deduplicated):
            _doc = {
                "_op_type": "index" if duplicate_documents == "overwrite" else "create",
                "_index": index,
                **doc.to_dict(field_map=self._create_document_field_map()),
            }  # type: Dict[str, Any]

            # cast embedding type as ES cannot deal with np.array
            if _doc[self.embedding_field] is not None:
                if type(_doc[self.embedding_field]) == np.ndarray:
                    _doc[self.embedding_field] = _doc[self.embedding_field].tolist()

            # rename id for elastic
            _doc["_id"] = str(_doc.pop("id"))

            # don't index query score and empty fields
            _ = _doc.pop("score", None)
            _doc = {k: v for k, v in _doc.items() if v is not None}

            # In order to have a flat structure in elastic + similar behaviour to the other DocumentStores,
            # we "unnest" all value within "meta"
            if "meta" in _doc.keys():
                for k, v in _doc["meta"].items():
                    _doc[k] = v
                _doc.pop("meta")
            documents_to_index.append(_doc)
        documents_to_index_chunk = split_list_in_chunck(documents_to_index, 9990)
        for doc_chunk in tqdm(documents_to_index_chunk):
            pb_ = parallel_bulk(self.client, 
                              doc_chunk, 
                              chunk_size=10000, 
                              thread_count=8, 
                              queue_size=8,
                              refresh=self.refresh_type, 
                              headers=headers)
            deque(pb_, maxlen=0)
            documents_to_index = []

In [22]:
document_store.write_documents_parallel = write_documents_parallel

In [23]:
%%script false --no-raise-error
all_docs = []
for i in range(0, 100):
    shard = wiki_corpus.shard(100, index=i)
    with tqdm(total=shard.shape[0]) as pbar:
        docs_in_shard = tqdm_asyncio.gather(*[convert_wiki_article_to_docs(item, clean_func=clean_wiki_text, split_paragraphs=True) for item in shard])
        all_docs.append(docs_in_shard)
    print("done with shard ", i)

In [24]:
from  functools import reduce
from operator import iconcat

In [25]:
%%script false --no-raise-error
with tqdm(total=len(all_docs)) as pbar:
     scan_results = await tqdm_asyncio.gather(*all_docs[90:100])

In [26]:
%%script false --no-raise-error
scan_results = reduce(iconcat, scan_results, [])
scan_results = reduce(iconcat, scan_results, [])

With our document indexted int the elastic searh we can search , use the piaf dataset which have question with answers without paragraph and leverage them.

#### Reading document from File

In [27]:
from haystack.nodes import TextConverter

In [28]:
from haystack.schema import Document
from secrets import token_hex

# @Todo: this is not working now , it was supposed to save the document to dataframe
def get_document_from_text(row):
    """numpy row with the text and the date of the post

    Args:
        row (_type_): _description_

    Returns:
        _type_: _description_
    """
    text = row[0].replace(u'\xa0', u' ')
    for paragraph in text.split("   "):
        if not paragraph.strip():  # skip empty paragraphs
            continue
        return Document(content=paragraph, meta={"posted_at":row[1] if row[1] else "" })

In [29]:
from haystack.errors import HaystackError
from haystack.schema import Document
from typing import List, Optional, Generator, Set, Union
from copy import deepcopy
from haystack.nodes import PreProcessor

class CustomPreProcessor(PreProcessor):
    def __init__(self, custom_preprocessor=None, **kwargs):
        super().__init__(**kwargs)
        self.custom_preprocessor = custom_preprocessor
    def clean(
        self,
        document: Union[dict, Document],
        clean_whitespace: bool,
        clean_header_footer: bool,
        clean_empty_lines: bool,
        remove_substrings: List[str],
        id_hash_keys: Optional[List[str]] = None,
    ) -> Document:
        """
        
        Perform document cleaning on a single document and return a single document. This method will deal with whitespaces, headers, footers
        and empty lines. Its exact functionality is defined by the parameters passed into PreProcessor.__init__().
        """
        if id_hash_keys is None:
            id_hash_keys = self.id_hash_keys

        if isinstance(document, dict):
            document = Document.from_dict(document, id_hash_keys=id_hash_keys)

        # Mainly needed for type checking
        if not isinstance(document, Document):
            raise HaystackError("Document must not be of type 'dict' but of type 'Document'.")
        text = document.content
        text = self.custom_preprocessor(text)
        if clean_header_footer:
            text = self._find_and_remove_header_footer(
                text, n_chars=300, n_first_pages_to_ignore=1, n_last_pages_to_ignore=1
            )

        if clean_whitespace:
            lines = text.splitlines()

            cleaned_lines = []
            for line in lines:
                line = line.strip()
                cleaned_lines.append(line)
            text = "\n".join(cleaned_lines)

        if clean_empty_lines:
            text = re.sub(r"\n\n+", "\n\n", text)

        for substring in remove_substrings:
            text = text.replace(substring, "")

        if text != document.content:
            document = deepcopy(document)
            document.content = text

        return document
    
    

In [30]:
from  functools import reduce
from operator import iconcat

With our document indexted int the elastic searh we can search , use the piaf dataset which have question with answers without paragraph and leverage them.

In [31]:
from collections import deque

In [32]:
import re
from gensim.utils import deaccent
from unicodedata import normalize as unicode_normalize

In [33]:
def replace_point(document):
    """replace the point with the wwt.www with space point before tokenizing the document .
    TOdos : this may have a a downside when the point is in the middle of a words
    Args:
        document (_type_): _description_
    """
    result = re.sub(r"(\S)\.(\S)", r"\1 . \2", document)
    return result

def replace_website_name(document):
    """sometimes the doucment has the name politico.cd or 7sur7.cd or actualite.cd, we would like to replace them by the 
    actual name of the website. before proper cleaning

    Args:
        document (_type_): _description_
    """
    # @TODO : not sure if this will work but , way better replace by the first line of match.
    
    result = re.sub(r"7SUR7.CD|politico.cd|actualite.cd|mediacongo.net", r"SITE_WEB", document, flags=re.IGNORECASE)
    return result

def remove_accents(document):
    input_without_accent = deaccent(document)
    return input_without_accent

def pre_clean_document(document):
    """pre clean the document by removing the accents and replacing the point with the wwt.www with space point before tokenizing the document .
    TOdos : this may have a a downside when the point is in the middle of a words
    and any other side of cleaning that we want to do .
    Args:
        document (_type_): _description_
    """
    result = remove_accents(document)
    result =  replace_website_name(result)
    result = replace_point(result)
    result = re.sub(r"This post has already been read \d+ times!", "", result) # remove unwanted text
    result = unicode_normalize("NFKD", result)
    return result

In [34]:
preprocessor = CustomPreProcessor(
    clean_empty_lines=True,
    clean_whitespace=True,
    clean_header_footer=False,
    split_by="word",
    split_length=200,
    split_respect_sentence_boundary=True,
    language="fr",
    custom_preprocessor=pre_clean_document,
)


cd_news_docs = preprocessor.process(all_cd_news_docs)


NameError: name 'all_cd_news_docs' is not defined

In [35]:

print(f"\nn_docs_output: {len(cd_news_docs)}")

NameError: name 'cd_news_docs' is not defined

In [36]:
write_documents_parallel(document_store, cd_news_docs)

NameError: name 'cd_news_docs' is not defined

In [37]:
%%script false --no-raise-error
write_documents_parallel(document_store, scan_results)

#### Retrieving Documents

This is the section where we will start working with our QA datasets,

##### PIAF Dataset

In [38]:
from haystack.nodes import BM25Retriever

In [39]:
bm25_retriever = BM25Retriever(document_store=document_store, all_terms_must_match=False)

In [40]:
import pandas as pd

In [41]:
from pathlib import Path
DATA_PATH = Path.cwd().parent.joinpath("data")
assert DATA_PATH.exists(), "the data path does not exist"

In [42]:
piaf_file = DATA_PATH.joinpath("piaf", "piaf-v1.1.json")

In [43]:
piaf_file_without_context = DATA_PATH.joinpath("piaf", "piaf-additional.csv")

In [44]:
assert piaf_file.exists(), "the piaf dataset does not exist"

In [45]:
assert piaf_file_without_context.exists()

piaf_question = data

In [46]:
piaf_df_without_context = pd.read_csv(piaf_file_without_context)

In [47]:
piaf_df_without_context.head()

question  \
0                 Quel architecte fût à l'origine des plans du Woolworth building?   
1  Où se trouvait Franck Woolworth lors de l'inauguration de son immeuble New Y...   
2                      Comment fût payé le bâtiment commandé par Franck Woolworth?   
3                                   En quelle année ouvrit le Woolworth Building ?   
4                             Qui commanda la construction du Woolworth Building ?   

           reponse  
0     Cass Gilbert  
1       Washington  
2          en cash  
3             1913  
4  Frank Woolworth

In [48]:
sample_question_response = piaf_df_without_context.sample(1)
question = deaccent(sample_question_response.question.values[0])
response = deaccent(sample_question_response.reponse.values[0])


In [49]:
question

"Qu'est ce qu'une tendinite ?"

In [50]:
from haystack.schema import EvaluationResult, MultiLabel, Document, Answer, Label

### Adding Additional Context to PIAF

With our dataset with context, let us pull more question with context for the original piaf dataset with context

In [51]:
from datasets import load_dataset

In [52]:
piaf_dataset = load_dataset("piaf")

WARNING - datasets.load -  Using the latest cached version of the module from /Users/es.py/.cache/huggingface/modules/datasets_modules/datasets/piaf/535c60f4155fe1d644c1746e86131963c082f309d0dbb5ba4d606786c7f4a6ae (last modified on Thu Jul 14 08:39:15 2022) since it couldn't be found locally at piaf., or remotely on the Hugging Face Hub.
WARNING - datasets.builder -  Reusing dataset piaf (/Users/es.py/.cache/huggingface/datasets/piaf/plain_text/1.0.0/535c60f4155fe1d644c1746e86131963c082f309d0dbb5ba4d606786c7f4a6ae)


  0%|          | 0/1 [00:00<?, ?it/s]

In [53]:
piaf_df = piaf_dataset["train"].to_pandas()
piaf_df.answers = piaf_df.answers.apply(lambda x : x["text"])

In [54]:
piaf_dataset.keys()

dict_keys(['train'])

In [55]:
piaf_df.head()

id  title  \
0  p140295443291664  Sport   
1  p140295443291520  Sport   
2  p140295443291376  Sport   
3  p140295443291088  Sport   
4  p140295443290872  Sport   

                                                                           context  \
0  Les dépenses des ménages représentent plus de 50 % de ces montants (14,2 mil...   
1  Les dépenses des ménages représentent plus de 50 % de ces montants (14,2 mil...   
2  Les dépenses des ménages représentent plus de 50 % de ces montants (14,2 mil...   
3  Les dépenses des ménages représentent plus de 50 % de ces montants (14,2 mil...   
4  Les dépenses des ménages représentent plus de 50 % de ces montants (14,2 mil...   

                                                   question           answers  
0  Combien de personnes travaillent au ministère des sports         [100 000]  
1                                      Combien d'employeurs          [20 000]  
2                           Quel part du budget des ménages              [50]  
3                                      Quel montant en 2003  [14,2 milliards]  
4                                      Quel montant en 2019    [12 milliards]

#### Evaluation Script of the retriever

This section will describe the evaluation script for the retriever model. Before writing the evaluation script, question and answer labels need to be created.

In this section, we will evaluate the retrieval model and check how it performed on our datasets.



In [56]:
piaf_df.loc[0, ['id', 'context', 'question', "answers"]].to_dict()

{'id': 'p140295443291664',
 'context': "Les dépenses des ménages représentent plus de 50 % de ces montants (14,2 milliards d'euros en 2003 et 12 milliards d'euros en 2019), contre 7,9 milliards d'euros pour les collectivités locales, 3,2 pour l'État, et 2,2 pour les entreprises. Parmi les dépenses sportives des ménages en 2003, 3,7 milliards sont consacrés aux vêtements de sport et chaussures, 2 aux biens durables, 2,7 aux autres biens et 5,8 aux services. Le Ministère de la Jeunesse et des Sports estime à 100 000 (58 % d'hommes pour 42 % de femmes) le nombre de salariés travaillant pour le secteur sportif en France pour quelque 20 000 employeurs.",
 'question': 'Combien de personnes travaillent au ministère des sports',
 'answers': array(['100 000'], dtype=object)}

In [82]:
def build_label(id, question, context, answers):
    doc = Document(content=deaccent(context), id=str(id))
    answer= Answer(answer=answers[0], type="generative")
    label = Label(id=str(id), 
                  query=deaccent(question), 
                  document=doc, 
                  is_correct_answer=True, 
                  answer=answer, 
                  is_correct_document=True, 
                  origin="gold-label")
    return label

In [83]:
build_label(**piaf_df.loc[0, ['id', 'context', 'question', "answers"]].to_dict())

{'id': 'p140295443291664', 'query': 'Combien de personnes travaillent au ministere des sports', 'document': {'content': "Les depenses des menages representent plus de 50 % de ces montants (14,2 milliards d'euros en 2003 et 12 milliards d'euros en 2019), contre 7,9 milliards d'euros pour les collectivites locales, 3,2 pour l'Etat, et 2,2 pour les entreprises. Parmi les depenses sportives des menages en 2003, 3,7 milliards sont consacres aux vetements de sport et chaussures, 2 aux biens durables, 2,7 aux autres biens et 5,8 aux services. Le Ministere de la Jeunesse et des Sports estime a 100 000 (58 % d'hommes pour 42 % de femmes) le nombre de salaries travaillant pour le secteur sportif en France pour quelque 20 000 employeurs.", 'content_type': 'text', 'id': 'p140295443291664', 'meta': {}, 'score': None, 'embedding': None}, 'is_correct_answer': True, 'is_correct_document': True, 'origin': 'gold-label', 'answer': {'answer': '100 000', 'type': 'generative', 'score': None, 'context': None

In [84]:
piaf_evaluation_labels = piaf_df.loc[:, ['id', 'context', 'question', "answers"]].apply(lambda x: build_label(**x.to_dict()), axis="columns")

#### Saving evaluation labels To ES

The code in this section saves the labels to the document store.

In [89]:
PIAF_LABEL_INDEX_NAME = 'piaf-label-index'

In [90]:
piaf_evaluation_labels = piaf_evaluation_labels.to_list()

AttributeError: 'list' object has no attribute 'to_list'

In [91]:
piaf_evaluation_labels[0]

{'id': 'p140295443291664', 'query': 'Combien de personnes travaillent au ministere des sports', 'document': {'content': "Les depenses des menages representent plus de 50 % de ces montants (14,2 milliards d'euros en 2003 et 12 milliards d'euros en 2019), contre 7,9 milliards d'euros pour les collectivites locales, 3,2 pour l'Etat, et 2,2 pour les entreprises. Parmi les depenses sportives des menages en 2003, 3,7 milliards sont consacres aux vetements de sport et chaussures, 2 aux biens durables, 2,7 aux autres biens et 5,8 aux services. Le Ministere de la Jeunesse et des Sports estime a 100 000 (58 % d'hommes pour 42 % de femmes) le nombre de salaries travaillant pour le secteur sportif en France pour quelque 20 000 employeurs.", 'content_type': 'text', 'id': 'p140295443291664', 'meta': {}, 'score': None, 'embedding': None}, 'is_correct_answer': True, 'is_correct_document': True, 'origin': 'gold-label', 'answer': {'answer': '100 000', 'type': 'generative', 'score': None, 'context': None

In [92]:
document_store.write_labels(labels=piaf_evaluation_labels, index=PIAF_INDEX_NAME)

[]
******************************


With this we have our labels saved in elasticsearch instance, we can now evaluate our retriever.

In [93]:
retriever_piaf_eval_results = bm25_retriever.eval(top_k=100, label_index=PIAF_LABEL_INDEX_NAME, doc_index=INDEX_NAME, open_domain=True)

INFO - haystack.nodes.retriever.base -  Performing eval queries...
  0%|                                                                                                                                                                                                                                                                                                  | 1/3812 [00:00<11:44,  5.41it/s]

Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Combien de personnes travaillent au ministere des sports', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': "Combien d'employeurs", 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}


  0%|▍                                                                                                                                                                                                                                                                                                 | 5/3812 [00:00<04:49, 13.16it/s]

Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Quel part du budget des menages', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Quel montant en 2003', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Quel montant en 2019', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'En quelle annee Jakob Bohme tombe-t-il malade ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}


  0%|▌                                                                                                                                                                                                                                                                                                 | 7/3812 [00:00<04:55, 12.87it/s]

...

Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': "Qu'a permit le principe de coevolution a pieride de la rave (Pieris rapae)?", 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Comment le puceron du chou detourne-t-il les defenses des plantes?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Pourquoi le puceron du chou est-il toxique pour Adalia bipunctata?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': "Par quel principe la pieride de la rave detourne-t-elle l'hydrolyse du glucosinolate?", 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi

100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▋| 3808/3812 [03:12<00:00, 23.00it/s]

Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Quels effets ont les huiles de moutarde sur les insectes', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Ou sont les glucosinolates', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': "En quelle annee les Americains doivent faire face a un bas niveau de reserves d'eau ?", 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Qui commandait la goelette Enterprise ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}


100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3812/3812 [03:13<00:00, 19.75it/s]
INFO - haystack.nodes.retriever.base -  For 1258 out of 3812 questions (33.00%), the answer was in the top-100 candidate passages selected by the retriever.


Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': "Comment l'Enterprise a-t-elle trompe l'ennemi ?", 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': "Dans quel pays Dale a-t-il ordonne d'aller se ravitailler ?", 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': "Quelle etait la nationalite du navire rencontre par l'Enterprise en route pour Malte ?", 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}


In [94]:
retriever_piaf_eval_results

{'recall': 0.3300104931794334,
 'map': 0.09025306838406492,
 'mrr': 0.12260737637465006,
 'retrieve_time': 516.7674288630151,
 'n_questions': 3812,
 'top_k': 100}

 
 For 1258 out of 3812 questions (33.00%) in the piaf dataset, the answer was in the top-100 candidate passages selected by the retriever.

###  Adding Additional Context to Fquad

This section deals with the FQuad dataset.

In [101]:
import json

In [98]:
frquad_path_train = DATA_PATH.joinpath("fquad", "train.json")
frquad_path_valid = DATA_PATH.joinpath("fquad", "valid.json")

In [99]:
assert frquad_path_train.exists()
assert frquad_path_valid.exists()

In [102]:
with open(frquad_path_train, "r") as f:
    frquad_train = json.load(f)

In [207]:
with open(frquad_path_valid, "r") as f:
    frquad_valid = json.load(f)

In [103]:
frquad_train = frquad_train.get("data")


In [208]:
frquad_valid = frquad_valid.get("data")

### Convert Squad Data to HayStack Document

this section will convert the Fquad dataset to haystack label for better evaluation.

In [192]:
from haystack.utils.squad_data import SquadData

In [200]:
class FQuadData(SquadData):
    """
    This class extend the base SquadData to accomodate the Fquad dataset.
    """
    @staticmethod
    def to_df(data):
        """Convert a list of SQuAD document dictionaries into a pandas dataframe (each row is one annotation)"""
        flat = []
        for document in data:
            title = document["title"]
            for paragraph in document["paragraphs"]:
                context = paragraph["context"]
                for question in paragraph["qas"]:
                    q = question["question"]
                    id = question["id"]
                    is_impossible = question.get("is_impossible", False)
                    # For no_answer samples
                    if len(question["answers"]) == 0:
                        flat.append({"title": title,
                                     "context": context,
                                     "question": q,
                                     "id": id,
                                     "answer_text": "",
                                     "answer_start": None,
                                     "is_impossible": is_impossible})
                    # For span answer samples
                    else:
                        for answer in question["answers"]:
                            answer_text = answer["text"]
                            answer_start = answer["answer_start"]
                            flat.append({"title": title,
                                         "context": context,
                                         "question": q,
                                         "id": id,
                                         "answer_text": answer_text,
                                         "answer_start": answer_start,
                                         "is_impossible": is_impossible})
        df = pd.DataFrame.from_records(flat)
        return df
    
    def to_label_objs(self, type="generative"):
        """Export all labels stored in this object to haystack.Label objects"""
        df_labels = self.df[["id", "question", "answer_text", "answer_start", "context"]]
        record_dicts = df_labels.to_dict("records")
        labels = [
            Label(
                query=deaccent(record["question"]),
                answer=Answer(answer=record["answer_text"], type="generative"),
                is_correct_answer=True,
                is_correct_document=True,
                id=f'fquad_{record["id"]}',
                origin=record.get("origin", "gold-label"),
                document=Document(content=record.get('context'), id=str(record['id']))
            ) for record in record_dicts
        ]
        return labels

In [201]:
fquad_data = FQuadData(frquad_train)

In [209]:
fquad_validation_data = FQuadData(frquad_valid)

In [202]:
fquad_train_labels = fquad_data.to_label_objs()

In [203]:
fquad_train_labels[1]

{'id': 'fquad_c2415641-9a62-4052-b57b-9a239da7599c', 'query': 'Quel astronome decouvrit Uranus ?', 'document': {'content': "L'idée selon laquelle une planète inconnue pourrait exister entre les orbites de Mars et Jupiter fut proposée pour la première fois par Johann Elert Bode en 1768. Ses suggestions étaient basées sur la loi de Titius-Bode, une théorie désormais obsolète proposée par Johann Daniel Titius en 1766,. Selon cette loi, le demi-grand axe de cette planète aurait été d'environ 2,8 ua. La découverte d'Uranus par William Herschel en 1781 accrut la confiance dans la loi de Titius-Bode et, en 1800, vingt-quatre astronomes expérimentés combinèrent leurs efforts et entreprirent une recherche méthodique de la planète proposée,. Le groupe était dirigé par Franz Xaver von Zach. Bien qu'ils n'aient pas découvert Cérès, ils trouvèrent néanmoins plusieurs autres astéroïdes.", 'content_type': 'text', 'id': 'c2415641-9a62-4052-b57b-9a239da7599c', 'meta': {}, 'score': None, 'embedding': No

In [204]:
fquad_data.df.id.duplicated().value_counts()

False    20129
True       604
Name: id, dtype: int64

In [211]:
fquad_validation_data.df.head()

title  \
0  anges-musiciens-(national-gallery)   
1  anges-musiciens-(national-gallery)   
2  anges-musiciens-(national-gallery)   
3  anges-musiciens-(national-gallery)   
4  anges-musiciens-(national-gallery)   

                                                                           context  \
0  Les deux tableaux sont certes décrits par des documents contemporains à leur...   
1  Les deux tableaux sont certes décrits par des documents contemporains à leur...   
2  Les deux tableaux sont certes décrits par des documents contemporains à leur...   
3  Les deux panneaux présentent de nombreuses similitudes : chacun comporte un ...   
4  Les deux panneaux présentent de nombreuses similitudes : chacun comporte un ...   

                                                                question  \
0                            Que concerne principalement les documents ?   
1                               Par quoi sont décrit les deux tableaux ?   
2  Quels types d'objets sont les deux tableaux aux yeux des chercheurs ?   
3                   Sur quelle jambe les personnages se tiennent-t-ils ?   
4                                  Quel pied avancent les personnages ?    

                                     id              answer_text  \
0  a524504f-0816-4f58-9f2d-27f82a85c73d    La Vierge aux rochers   
1  8a72ad1c-b2fe-4fe6-9f87-35fcb713cf38  documents contemporains   
2  b2db7f77-f6a7-4c3d-9274-9807f9764e97   objets de spéculations   
3  31ec5079-7d62-43b9-8a5c-49f8b7ad6f5a                   droite   
4  008a2ca6-a589-4751-ba59-f7f762874785                   gauche   

   answer_start  is_impossible  
0           161          False  
1            46          False  
2           204          False  
3           242          False  
4           271          False

In [212]:
fquad_validation_data_labels = fquad_validation_data.to_label_objs()

In [205]:
FQUAD_TRAIN_LABEL_INDEX = 'fquad-train-label-index'
FQUAD_TEST_LABEL_INDEX = 'fquad-test-label-index'

In [206]:
document_store.write_labels(labels=fquad_train_labels, index=FQUAD_TRAIN_LABEL_INDEX)

/Users/es.py/Projects/Personal/unsupervised-open-domain-french-question-answering/.venv/lib/python3.9/site-packages/elasticsearch/connection/base.py:190: ElasticsearchDeprecationWarning: Elasticsearch built-in security features are not enabled. Without authentication, your cluster could be accessible to anyone. See https://www.elastic.co/guide/en/elasticsearch/reference/7.16/security-minimal-setup.html to enable security.
  warnings.warn(message, category=ElasticsearchDeprecationWarning)
WARNING - haystack.document_stores.elasticsearch -  Duplicate Label IDs: Inserting a Label whose id already exists in this document store. This will overwrite the old Label. Please make sure Label.id is a unique identifier of the answer annotation and not the question.


['fquad_5c59e19a-066c-4dc0-aa16-2871dcb12d39', 'fquad_5c59e19a-066c-4dc0-aa16-2871dcb12d39', 'fquad_896bc528-a91b-435e-822f-55b1675454da', 'fquad_896bc528-a91b-435e-822f-55b1675454da', 'fquad_896bc528-a91b-435e-822f-55b1675454da', 'fquad_3f934ce0-c8cf-49b6-898b-2254c60ca97e', 'fquad_3f934ce0-c8cf-49b6-898b-2254c60ca97e', 'fquad_05c514bb-0d00-4c51-9523-b3ab17c13227', 'fquad_05c514bb-0d00-4c51-9523-b3ab17c13227', 'fquad_05c514bb-0d00-4c51-9523-b3ab17c13227', 'fquad_781ef943-2516-41c1-802f-f923c09b2f5c', 'fquad_781ef943-2516-41c1-802f-f923c09b2f5c', 'fquad_411056f0-64d1-41bf-8df2-833492a9f552', 'fquad_411056f0-64d1-41bf-8df2-833492a9f552', 'fquad_502a2d98-3c69-4fe1-8c87-064e45804318', 'fquad_502a2d98-3c69-4fe1-8c87-064e45804318', 'fquad_ef0e3a31-5cee-429b-a01a-be3340dd2e96', 'fquad_ef0e3a31-5cee-429b-a01a-be3340dd2e96', 'fquad_fdc12e01-8535-474a-a4d2-0d7910013f02', 'fquad_fdc12e01-8535-474a-a4d2-0d7910013f02', 'fquad_bbe2da6f-c22c-44da-aa35-595ce6b2edb7', 'fquad_bbe2da6f-c22c-44da-aa35-59

In [213]:
document_store.write_labels(labels=fquad_validation_data_labels, index=FQUAD_TEST_LABEL_INDEX)

/Users/es.py/Projects/Personal/unsupervised-open-domain-french-question-answering/.venv/lib/python3.9/site-packages/elasticsearch/connection/base.py:190: ElasticsearchDeprecationWarning: Elasticsearch built-in security features are not enabled. Without authentication, your cluster could be accessible to anyone. See https://www.elastic.co/guide/en/elasticsearch/reference/7.16/security-minimal-setup.html to enable security.
  warnings.warn(message, category=ElasticsearchDeprecationWarning)


[]
******************************


In [214]:
retriever_fquad_train_results = bm25_retriever.eval(top_k=100, 
                                            label_index=FQUAD_TRAIN_LABEL_INDEX, 
                                            doc_index=INDEX_NAME, open_domain=True)

/Users/es.py/Projects/Personal/unsupervised-open-domain-french-question-answering/.venv/lib/python3.9/site-packages/elasticsearch/connection/base.py:190: ElasticsearchDeprecationWarning: Elasticsearch built-in security features are not enabled. Without authentication, your cluster could be accessible to anyone. See https://www.elastic.co/guide/en/elasticsearch/reference/7.16/security-minimal-setup.html to enable security.
  warnings.warn(message, category=ElasticsearchDeprecationWarning)
INFO - haystack.nodes.retriever.base -  Performing eval queries...
  0%|                                                                                                                                                                                                                                                                                                         | 0/20095 [00:00<?, ?it/s]

Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': "Quel astronome a emit l'idee en premier d'une planete entre les orbites de Mars et Jupiter ?", 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}


  0%|                                                                                                                                                                                                                                                                                                 | 3/20095 [00:00<44:37,  7.50it/s]

Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Quel astronome decouvrit Uranus ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Quelles furent les decouvertes finales des vingt-quatre astronomes ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Combien de fois Piazzi est-il parvenu a observer Ceres ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}


  0%|                                                                                                                                                                                                                                                                                                 | 5/20095 [00:00<34:37,  9.67it/s]

...

Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'A qui les etrusques ont transmis leur propre pantheon ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Quand les etrusques ont-ils ete assimiles a la republique romaine ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': "Qui rapporte une these de l'origine orientale des etrusques ?", 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Quelle est la these de Denys ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Comment se nomment les acteurs professionnels romain ?', 't

100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▉| 20091/20095 [15:28<00:00, 27.39it/s]

Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': "Qu'est-ce qui commence en 1731 ?", 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': "A qui est ouverte l'academie de Cortone ?", 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Qui publie un ouvrage en 1810 ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Quel pape organise un musee gregorien ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Ou se trouve le musee gregorien ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size'

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 20095/20095 [15:28<00:00, 21.65it/s]
INFO - haystack.nodes.retriever.base -  For 8384 out of 20095 questions (41.72%), the answer was in the top-100 candidate passages selected by the retriever.


Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Quand se poursuit la confection de faux ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}


In [215]:
retriever_fquad_valid_results = bm25_retriever.eval(top_k=100, 
                                            label_index=FQUAD_TEST_LABEL_INDEX, 
                                            doc_index=INDEX_NAME, open_domain=True)

INFO - haystack.nodes.retriever.base -  Performing eval queries...
  0%|▏                                                                                                                                                                                                                                                                                                 | 2/3184 [00:00<02:48, 18.90it/s]

Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Que concerne principalement les documents ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Par quoi sont decrit les deux tableaux ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': "Quels types d'objets sont les deux tableaux aux yeux des chercheurs ?", 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Sur quelle jambe les personnages se tiennent-t-ils ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Quel pied avancent les personnages ? ', 'type': 'most_fields', 'fiel

  0%|▋                                                                                                                                                                                                                                                                                                 | 8/3184 [00:00<02:08, 24.74it/s]

Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': "De quelle couleur est l'ange qui joue de la lira da braccio ?", 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': "D'ou sont issus les deux panneaux ?", 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Lors de quel processus des craquelures apparaissent ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': "Qu'est ce qui est utilise pour la finition des contours des figures ?", 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Quel est le nom du panneau central du retable ?', 'typ

  0%|█▎                                                                                                                                                                                                                                                                                               | 14/3184 [00:00<02:13, 23.81it/s]

...

Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': "Pour quelle partie de l'edifice l'association s'est-elle lancee dans la recherche d'aides et de subvention ?", 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'De quelle forme est la nef ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'de quelle forme est le chevet ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Dans quel direction le chevet est-il decale ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': "Que signifie le fait que l'eglise est orientee ?", 'type': '

100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▍| 3178/3184 [02:13<00:00, 20.34it/s]

Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': "Que caracterise l'emplacement de la porte dans le mur dirige vers le sud ?", 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'A quel risque la zone ou se situe la chapelle est-elle exposee ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Comment etait disposes les murets par rapport au courant ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}


100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3184/3184 [02:14<00:00, 23.74it/s]
INFO - haystack.nodes.retriever.base -  For 1272 out of 3184 questions (39.95%), the answer was in the top-100 candidate passages selected by the retriever.


Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'En quelle matiere sont les dalles du canal ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'Par quoi le canal est-il double ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}
Retriever query: {'size': '100', 'query': {'bool': {'must': [{'multi_match': {'query': 'A quoi devaient servir les terrasses ?', 'type': 'most_fields', 'fields': ['content'], 'operator': 'OR'}}]}}}


This is interesting, because now we have issues, the retriever was only able to find answers for 41%  of questions in the train dataset and for 40% of question in the test dataset.

In [ ]:
with open(frquad_path_valid, "r") as f:
    frquad_valid = json.load(f)

In [ ]:
frquad_valid = frquad_valid.get("data")

In [ ]:
fquad_path = DATA_PATH.joinpath("corpus", "french-qa", "fquad-with-multi-context")
fquad_path_output_train = fquad_path.joinpath("train")
fquad_path_output_valid = fquad_path.joinpath("valid")

In [ ]:
fquad_path_with_supporting = DATA_PATH.joinpath("corpus", "french-qa", "fquad-with-multi-context-with-without-answers")
fquad_path_output_supporting_train = fquad_path_with_supporting.joinpath("train")
fquad_path_output_supporting_valid = fquad_path_with_supporting.joinpath("valid")

In [ ]:
fquad_path_with_supporting.mkdir(exist_ok=True)

In [ ]:
for doc in frquad_train[0:2]:
    print(doc.get("title"))

In [ ]:
async def process_fquad_paragraph(retriever, paragraph, title, validate_answers,path ):
    """
    this will loop over the  a paragraph in fQuad dataset.
    since each paragraph have a list of question ,
     it will return query the elasticsearch for each batch of question 
    and return the additional related_context

    Args:
        paragraph (_type_): _description_
    """
    context  = paragraph.get("context")
    question_answers = paragraph.get("qas")
    ids = [qa.get("id") for qa in question_answers]
    questions = [qa.get("question") for qa in question_answers]
    answers = [qa.get("answers")[0].get("text") for qa in question_answers]
    retrieved_docs = retriever.retrieve_batch(queries=questions, top_k=10)
    instances = process_answers(ids=ids, 
                                questions=questions,
                                titles=repeat(title, len(questions)),
                                answers=answers,
                                contexts=repeat(context, len(questions)),
                                retrieved_docs=retrieved_docs,
                                validate_answers=validate_answers)
    save_to_json(instances, path)

In [ ]:
assert fquad_path.exists()

In [ ]:
def check_answer_in_retrieved_docs(answer, retrieved_docs):
    for doc in retrieved_docs:
        if answer in doc.content:
            print(doc)
            return True
    return False

In [ ]:
async def process_fquad(fquad, path, retriever):
    all_article_processor = list()
    for document in tqdm_asyncio(fquad):
        title = document.get("title")
        paragraphs = document.get("paragraphs")
        doc_coroutine = tqdm_asyncio.gather(*[process_fquad_paragraph(retriever=bm25_retriever, paragraph=paragraph, title=title, validate_answers=False, path=path) for paragraph in paragraphs])
        all_article_processor.append(doc_coroutine)
    return await tqdm_asyncio.gather(*all_article_processor)

In [ ]:
await process_fquad(frquad_train, fquad_path_output_supporting_train, bm25_retriever)

In [ ]:
await process_fquad(frquad_valid, fquad_path_output_supporting_valid, bm25_retriever)

In [ ]:
def save_doc_to_json(doc, file):
    "saves an iterator of multiple json files to files in the path directory"
    with open(file, "w") as f:
        json.dump(doc, f, indent=4, ensure_ascii=False)

In [ ]:
def count_positive_context(path):
    json_files = path.glob('**/*.json')
    document_with_more = 0
    for file in json_files:
        with open(file, "r") as buffer:
            json_doc = json.load(buffer)
            contexts = json_doc["contexts"]
            if len(contexts) >1 :
                document_with_more +=1
    return document_with_more

In [ ]:
count_piaf = count_positive_context(piaf_with_multi_context_path)

In [ ]:
count_train_fquad = count_positive_context(fquad_path_output_train)

In [ ]:
count_valid_fquad = count_positive_context(fquad_path_output_valid)

In [ ]:
count_train_fquad

In [ ]:
count_valid_fquad

In [ ]:
count_piaf